In [31]:
!pip install gadm hdx-python-api

In [2]:
!pip install --upgrade geopandas fiona

   ---------------------------------------- 0.0/16.2 MB ? eta -:--:--
   ---------------------------------------- 0.0/16.2 MB ? eta -:--:--
   ---------------------------------------- 0.0/16.2 MB ? eta -:--:--
   ---------------------------------------- 0.0/16.2 MB ? eta -:--:--
    --------------------------------------- 0.3/16.2 MB ? eta -:--:--
    --------------------------------------- 0.3/16.2 MB ? eta -:--:--
    --------------------------------------- 0.3/16.2 MB ? eta -:--:--
   - -------------------------------------- 0.5/16.2 MB 372.9 kB/s eta 0:00:42
   - -------------------------------------- 0.5/16.2 MB 372.9 kB/s eta 0:00:42
   - -------------------------------------- 0.5/16.2 MB 372.9 kB/s eta 0:00:42
   - -------------------------------------- 0.5/16.2 MB 372.9 kB/s eta 0:00:42
   - -------------------------------------- 0.8/16.2 MB 381.3 kB/s eta 0:00:41
   - -------------------------------------- 0.8/16.2 MB 381.3 kB/s eta 0:00:41
   - -------------------------------

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gadm 0.0.5 requires geopandas==0.9.0, but you have geopandas 1.0.1 which is incompatible.


In [3]:
!pip install folium

In [33]:
import folium as fl
import pandas as pd
import geopandas as gpd
from hdx.api.configuration import Configuration
from hdx.data.resource import Resource
import urllib.request
import requests
import json
import requests
import itertools
from shapely.geometry import Polygon,MultiPolygon
import os
import time
import numpy as np
from gadm import GADMDownloader

In [34]:
# Initialize the GADMDownloader with the specified version (in this case, version 4.0)
downloader = GADMDownloader(version="4.0")

# Define the country name for which you want to retrieve administrative boundary data
country_name = "USA"

# Specify the administrative level you are interested in (e.g., 1 for districts or provinces)
ad_level = 2

# Retrieve the geospatial data for the selected country and administrative level
copygdf = downloader.get_shape_data_by_country_name(country_name=country_name, ad_level=ad_level)

In [35]:
copygdf.head(5)

ID_0        COUNTRY   NAME_1 NL_NAME_1       ID_2   NAME_2 VARNAME_2  \
0  USA  United States  Alabama            USA.1.1_1  Autauga             
1  USA  United States  Alabama            USA.1.2_1  Baldwin             
2  USA  United States  Alabama            USA.1.3_1  Barbour             
3  USA  United States  Alabama            USA.1.4_1     Bibb             
4  USA  United States  Alabama            USA.1.5_1   Blount             

  NL_NAME_2  TYPE_2 ENGTYPE_2 CC_2    HASC_2  \
0            County    County       US.AL.AU   
1            County    County       US.AL.BD   
2            County    County       US.AL.BR   
3            County    County       US.AL.BI   
4            County    County       US.AL.BU   

                                            geometry  
0  MULTIPOLYGON (((-86.91668 32.66431, -86.82678 ...  
1  MULTIPOLYGON (((-87.74416 30.29445, -87.74389 ...  
2  MULTIPOLYGON (((-85.41607 31.61962, -85.49133 ...  
3  MULTIPOLYGON (((-87.42078 32.87446, -87.42028 ...  
4  MULTIPOLYGON (((-86.96287 33.85858, -86.96512 ...

In [72]:
gdf = copygdf

In [73]:
gdf['NAME_1'].unique()

array(['Alabama', 'Alaska', 'Arizona', 'Arkansas', 'California',
       'Colorado', 'Connecticut', 'Delaware', 'District of Columbia',
       'Florida', 'Georgia', 'Hawaii', 'Idaho', 'Illinois', 'Indiana',
       'Iowa', 'Kansas', 'Kentucky', 'Louisiana', 'Maine', 'Maryland',
       'Massachusetts', 'Michigan', 'Minnesota', 'Mississippi',
       'Missouri', 'Montana', 'Nebraska', 'Nevada', 'New Hampshire',
       'New Jersey', 'New Mexico', 'New York', 'North Carolina',
       'North Dakota', 'Ohio', 'Oklahoma', 'Oregon', 'Pennsylvania',
       'Rhode Island', 'South Carolina', 'South Dakota', 'Tennessee',
       'Texas', 'Utah', 'Vermont', 'Virginia', 'Washington',
       'West Virginia', 'Wisconsin', 'Wyoming'], dtype=object)

In [74]:
gdf = gdf[gdf['NAME_1']=='Massachusetts']

In [75]:
gdf['NAME_2'].unique()

array(['Barnstable', 'Berkshire', 'Bristol', 'Dukes', 'Essex', 'Franklin',
       'Hampden', 'Hampshire', 'Middlesex', 'Nantucket', 'Norfolk',
       'Plymouth', 'Suffolk', 'Worcester'], dtype=object)

In [76]:
gdf = gdf[gdf['NAME_2']=='Plymouth']

In [77]:
selected_gdf = gdf

In [79]:
selected_gdf

ID_0        COUNTRY         NAME_1 NL_NAME_1         ID_2    NAME_2  \
1226  USA  United States  Massachusetts            USA.22.12_1  Plymouth   

     VARNAME_2 NL_NAME_2  TYPE_2 ENGTYPE_2 CC_2    HASC_2  \
1226                      County    County       US.MA.PL   

                                               geometry  
1226  MULTIPOLYGON (((-70.80222 41.61836, -70.80222 ...

In [80]:
from IPython.display import display, HTML

# Inject custom CSS to prevent overflow and ensure the map container fits properly
display(HTML("""
    <style>
        .map-container {
            width: 60% !important;  /* Adjust width as needed */
            height: 40% !important; /* Adjust height as needed */
            margin: 0 auto;         /* Center the map */
            border: 2px solid black; /* Optional: to visualize the map container */
        }
        .leaflet-container {
            width: 60% !important;  /* Make sure the leaflet map takes up the full width of the container */
            height: 40% !important; /* Full height within the container */
        }
    </style>
"""))

# Create a Folium map with a temporary zoom level
m = fl.Map(zoom_start=1, tiles="OpenStreetMap")

# Get the bounds (bounding box) of the geometries in selected_gdf
bounds = selected_gdf.total_bounds  # Returns [minx, miny, maxx, maxy]

# Set the map's location and zoom to fit the bounds
m.fit_bounds([[bounds[1], bounds[0]], [bounds[3], bounds[2]]])

# Iterate through each row in the geospatial data (gdf) representing administrative boundaries
for _, r in selected_gdf.iterrows():
    # Simplify the geometry of the current boundary with a specified tolerance
    sim_geo = gpd.GeoSeries(r["geometry"]).simplify(tolerance=0.0001)
    # Convert the simplified geometry to JSON format
    geo_j = sim_geo.to_json()

    # Create a GeoJson layer from the JSON geometry, and style it with a red fill color
    geo_j = fl.GeoJson(data=geo_j, style_function=lambda x: {"fillColor": "red"})

    # Add a popup with the NAME_3 attribute (administrative region name) to the GeoJson layer
    fl.Popup(r["NAME_2"]).add_to(geo_j)

    # Add the styled GeoJson layer to the Folium map (m)
    geo_j.add_to(m)

# Display the map wrapped in a custom div to control size
display(HTML('<div class="map-container">' + m._repr_html_() + '</div>'))


In [81]:
df = pd.read_csv("./ppp_USA_2020_1km_Aggregated_UNadj.csv")

In [82]:
df.head()

X          Y    Z
0 -156.488749  71.387083  0.0
1 -156.480416  71.387083  0.0
2 -156.472083  71.387083  0.0
3 -156.463749  71.387083  0.0
4 -156.455416  71.387083  0.0

In [83]:
pop = df.reset_index()

In [84]:
pop.head()

index           X          Y    Z
0      0 -156.488749  71.387083  0.0
1      1 -156.480416  71.387083  0.0
2      2 -156.472083  71.387083  0.0
3      3 -156.463749  71.387083  0.0
4      4 -156.455416  71.387083  0.0

In [85]:
pop.columns = ['ID','xcoord','ycoord','population']
pop['population'] = pop['population'].astype(int)
pop = gpd.GeoDataFrame(pop,geometry=gpd.points_from_xy(x=pop.xcoord, y=pop.ycoord))

In [86]:
pop.head(10)

ID      xcoord     ycoord  population                     geometry
0   0 -156.488749  71.387083           0  POINT (-156.48875 71.38708)
1   1 -156.480416  71.387083           0  POINT (-156.48042 71.38708)
2   2 -156.472083  71.387083           0  POINT (-156.47208 71.38708)
3   3 -156.463749  71.387083           0  POINT (-156.46375 71.38708)
4   4 -156.455416  71.387083           0  POINT (-156.45542 71.38708)
5   5 -156.447083  71.387083           0  POINT (-156.44708 71.38708)
6   6 -156.438749  71.387083           0  POINT (-156.43875 71.38708)
7   7 -156.488749  71.378750           0  POINT (-156.48875 71.37875)
8   8 -156.480416  71.378750           0  POINT (-156.48042 71.37875)
9   9 -156.472083  71.378750           0  POINT (-156.47208 71.37875)

In [87]:
print('Total Population:',round(pop['population'].sum()/1000000,2),'million')

Total Population: 327.98 million


Total population in Plymouth

In [88]:
population_aoi = gpd.sjoin(pop, selected_gdf, predicate='within')
print('Total Population (Area of Interest - Plymouth):',round(population_aoi['population'].sum()))

C:\Users\vijay\AppData\Local\Temp\ipykernel_24680\4070574832.py:1: UserWarning: CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: None
Right CRS: EPSG:4326

  population_aoi = gpd.sjoin(pop, selected_gdf, predicate='within')


Total Population (Area of Interest - Plymouth): 488104


In [89]:
print(population_aoi.head())

              ID     xcoord     ycoord  population  \
7986307  7986307 -70.930416  42.303750           0   
7986308  7986308 -70.922083  42.303750          22   
7986309  7986309 -70.913750  42.303750         380   
7986310  7986310 -70.905416  42.303750         562   
7992139  7992139 -70.880416  42.295417        1379   

                           geometry  index_right ID_0        COUNTRY  \
7986307  POINT (-70.93042 42.30375)         1226  USA  United States   
7986308  POINT (-70.92208 42.30375)         1226  USA  United States   
7986309  POINT (-70.91375 42.30375)         1226  USA  United States   
7986310  POINT (-70.90542 42.30375)         1226  USA  United States   
7992139  POINT (-70.88042 42.29542)         1226  USA  United States   

                NAME_1 NL_NAME_1         ID_2    NAME_2 VARNAME_2 NL_NAME_2  \
7986307  Massachusetts            USA.22.12_1  Plymouth                       
7986308  Massachusetts            USA.22.12_1  Plymouth                       
79863

In [91]:
selected_gdf

ID_0        COUNTRY         NAME_1 NL_NAME_1         ID_2    NAME_2  \
1226  USA  United States  Massachusetts            USA.22.12_1  Plymouth   

     VARNAME_2 NL_NAME_2  TYPE_2 ENGTYPE_2 CC_2    HASC_2  \
1226                      County    County       US.MA.PL   

                                               geometry  
1226  MULTIPOLYGON (((-70.80222 41.61836, -70.80222 ...

In [102]:
print(population_aoi.describe())

                 ID       xcoord       ycoord   population  index_right
count  2.797000e+03  2797.000000  2797.000000  2797.000000       2797.0
mean   8.237116e+06   -70.812525    41.951286   174.509832       1226.0
std    1.041647e+05     0.120514     0.144915   288.419726          0.0
min    7.986307e+06   -71.072083    41.628750     0.000000       1226.0
25%    8.151446e+06   -70.897083    41.837083    25.000000       1226.0
50%    8.240691e+06   -70.813750    41.945417    92.000000       1226.0
75%    8.318776e+06   -70.730416    42.070417   210.000000       1226.0
max    8.472690e+06   -70.530416    42.303750  3898.000000       1226.0


In [158]:
import folium as fl
import geopandas as gpd

# Create a base map
m = fl.Map(zoom_start=12, tiles="OpenStreetMap")

# Get the bounds (bounding box) of the geometries in selected_gdf
bounds = selected_gdf.total_bounds  # Returns [minx, miny, maxx, maxy]

# Set the map's location and zoom to fit the bounds
m.fit_bounds([[bounds[1], bounds[0]], [bounds[3], bounds[2]]])

# Iterate through each row in the geospatial data representing the boundary of Plymouth
for _, r in selected_gdf.iterrows():
    # Simplify the geometry of the current boundary with a specified tolerance
    sim_geo = gpd.GeoSeries(r["geometry"]).simplify(tolerance=0.0001)
    # Convert the simplified geometry to JSON format
    geo_j = sim_geo.to_json()

    # Create a GeoJson layer from the JSON geometry, and style it with a light fill color
    geo_j = fl.GeoJson(data=geo_j, style_function=lambda x: {"fillColor": "#ffffcc", "color": "black", "weight": 2, "fillOpacity": 0.3})

    # Add a popup with the NAME_2 attribute (administrative region name) to the GeoJson layer
    fl.Popup(r["NAME_2"]).add_to(geo_j)

    # Add the styled GeoJson layer to the Folium map (m)
    geo_j.add_to(m)

import matplotlib.pyplot as plt
import matplotlib.colors as mcolors

# Assuming population_aoi DataFrame is already defined and contains the population data
# Define the colormap and normalization
vmin = np.log1p(population_aoi['population'].min()+1)  # Minimum population value
vmax = np.log1p(population_aoi['population'].max())  # Maximum population value

# Create a colormap
cmap = plt.get_cmap("OrRd")  # You can choose any colormap you prefer
norm = mcolors.LogNorm(vmin=vmin, vmax=vmax)

# Add population data from population_aoi as gradient color for each point
for _, row in population_aoi.iterrows():
    # Get the coordinates
    coords = (row['ycoord'], row['xcoord'])  # Latitude first, then Longitude

    # Define a gradient color based on population
    population_value = row['population']
    if population_value > 0:
        fill_color = mcolors.rgb2hex(cmap(norm(np.log1p(population_value)))[:3])  # Convert to hex color
    else:
        fill_color = "#ffb68700"  # Default color for zero population

    # Create a small circle to represent the population point with gradient color
    fl.CircleMarker(
        location=coords,
        radius=2*max(2, np.log1p(population_value) / 5),  # Adjust the size based on population
        color=fill_color,
        fill=True,
        fill_opacity=0.7,
        opacity=0.4,  # Set border opacity
        popup=f"Population: {population_value}"  # Optional: show population value in popup
    ).add_to(m)
    
# Display the map
m
